

```
# This is formatted as code
```

#<font color="blue">**Clouds workshop**</font>

##your name: first last


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
ls drive/MyDrive/Colab


In [ ]:

import matplotlib.pyplot as plt
import numpy as np
import os
import pickle
from scipy.integrate import solve_ivp
from scipy import optimize
from scipy.stats import linregress
import xarray as xr


##<font color="green"> 1) Build the simple energy balance model with cloud feedbacks from class</font>



In [ ]:
########################################################################
def rhs(time,T,C_ocn,C_atm,CO2_initial,CO2_fixed,Delta_SW,Delta_LW):
    ########################################################################
    # right hand side of the equations for T_ocn and T_a:
    T_ocn=T[0]
    T_a=T[1]
    # calculate the RHS of both equations (rhs is an array of two elements):
    rhs=np.array([(S*(1-alpha(T_ocn,Delta_SW))+epsilon(T_a,Delta_LW,CO2_initial,CO2_fixed,time)*sigma*T_a**4-sigma*T_ocn**4)/C_ocn,
        (epsilon(T_a,Delta_LW,CO2_initial,CO2_fixed,time)*sigma*T_ocn**4-2*epsilon(T_a,Delta_LW,CO2_initial,CO2_fixed,time)*sigma*T_a**4)/C_atm])
    return rhs

########################################################################
def alpha(T,Delta_SW):
    # albedo as function of temperature representing low cloud effects
    ########################################################################
    alpha0=0.3
    alph=alpha0*(1+Delta_SW*(T-T_ref))
    return alph


########################################################################
def epsilon(T_a,Delta_LW,CO2_initial,CO2_fixed,time):
    # atmospheric emissivity as function of temperature, representing high cloud effects
    ########################################################################
    epsilon0=0.75+0.05*np.log2(CO2(CO2_initial,CO2_fixed,time)/280)
    eps=epsilon0*(1+Delta_LW*(T_a-T_a_ref))
    return np.minimum(1.0,eps)


########################################################################
def CO2(CO2_initial,CO2_fixed,time):
    # atmospheric CO2 as function of time;
    # if CO2_fixed=True, CO2_initial is used for all times.
    ########################################################################
    if CO2_fixed:
        CO2=CO2_initial
    else:
        CO2=CO2_initial*np.exp(time/(150*year))
    return np.minimum(CO2,560)

In [ ]:
########################################################################
## Main program starts here.
########################################################################

# set parameters:
year=365*24*3600;
time_max=200*year;
Cp_w=4000
rho_w=1000
C_ocn=Cp_w*rho_w*50 #CHANGE
C_atm=C_ocn/5 #CHANGE
sigma=5.67e-8
S=1361/4
CO2_initial=280
T_ref=281.41
T_a_ref=236.64


# run the energy balance model to steady state for CO2=280
# to get initial conditions for warming scenario:
# ---------------------------------------------------------
T_init=[280,250] # initial conditions
teval=np.arange(0,time_max,time_max/100)
tspan=(teval[0],teval[-1])
# without feedbacks:
Delta_SW=0.0  # try -0.02 to 0.1 #CHANGE
Delta_LW=0.0  # try +/- 0.02. #CHANGE
CO2_fixed=True
sol = solve_ivp(fun=lambda time,T: rhs(time,T,C_ocn,C_atm,CO2_initial,CO2_fixed,Delta_SW,Delta_LW) \
                ,vectorized=False,y0=T_init,t_span=tspan,t_eval=teval,rtol=1.0e-6)
time_no_feedback=sol.t
T_280=sol.y[:,-1]
T_ref=T_280[0]
T_a_ref=T_280[1]
print("steady temperature (surface/atmosphere) at CO2=280:",T_280)

In [ ]:
# run the energy balance model in time-dependent warming scenario:
# ----------------------------------------------------------------
T_init=[T_ref,T_a_ref] # initial conditions
teval=np.arange(0,time_max,time_max/100)
tspan=(teval[0],teval[-1])
# without feedbacks:
Delta_SW=0.0
Delta_LW=0.0
CO2_fixed=False
sol = solve_ivp(fun=lambda time,T: rhs(time,T,C_ocn,C_atm,CO2_initial,CO2_fixed,Delta_SW,Delta_LW) \
                ,vectorized=False,y0=T_init,t_span=tspan,t_eval=teval,rtol=1.0e-6)
time_no_feedback=sol.t
T_no_feedback=sol.y
# with feedbacks:
Delta_SW=-0.01 #CHANGE -0.01
Delta_LW=0.001 #CHANE 0.001
CO2_fixed=False
sol = solve_ivp(fun=lambda time,T: rhs(time,T,C_ocn,C_atm,CO2_initial,CO2_fixed,Delta_SW,Delta_LW) \
                ,vectorized=False,y0=T_init,t_span=tspan,t_eval=teval,rtol=1.0e-6)
time=sol.t
T=sol.y


# save model output to be plotted:
# --------------------------------
T_plot=np.zeros(len(T[0,:]))
T_a_plot=np.zeros(len(T[0,:]))
T_plot_no_feedback=np.zeros(len(T[0,:]))
T_a_plot_no_feedback=np.zeros(len(T[0,:]))
alpha_plot=np.zeros(len(T[0,:]))
epsilon_plot=np.zeros(len(T[0,:]))
CO2_plot=np.zeros(len(T[0,:]))
i=0;
for t in T_plot:
    T_plot[i]=T[0,i];
    T_a_plot[i]=T[1,i];
    T_plot_no_feedback[i]=T_no_feedback[0,i];
    T_a_plot_no_feedback[i]=T_no_feedback[1,i];
    alpha_plot[i]=alpha(T[0,i],Delta_SW)
    epsilon_plot[i]=epsilon(T[1,i],Delta_LW,CO2_initial,CO2_fixed,time[i])
    CO2_plot[i]=CO2(CO2_initial,CO2_fixed,time[i])
    i=i+1;

N=len(T_plot)

In [ ]:
########################################################################
## plots:
########################################################################

fig1=plt.figure(1,figsize=(8,4),dpi=150)

plt.subplot(2,2,1)
plt.plot(time_no_feedback/year,CO2_plot,'b-')
#plt.xlabel('years');
plt.ylabel('CO$_2$ (ppm)');
plt.grid(lw=0.25)
axes=plt.gca()



plt.subplot(2,2,2)
h1=plt.plot(time/year,alpha_plot,'b-',markersize=1,label="$\\alpha$")
plt.grid(lw=0.25)
axis1=plt.gca()
axis2 =axis1.twinx()
h2=axis2.plot(time/year,epsilon_plot,'r-',markersize=1,label="$\\epsilon$")
#plt.xlabel('years');
#plt.ylabel('nondim');
#plt.title('albedo, emissivity');
# added these three lines
h = h1+h2
legend_labels = [l.get_label() for l in h]
axis1.legend(h, legend_labels, loc="center right")
axis1.tick_params(axis='y', labelcolor="b")
axis2.tick_params(axis='y', labelcolor="r")
axes=plt.gca()



plt.subplot(2,2,3)
plt.plot(time_no_feedback/year,T_plot_no_feedback,'b--',markersize=1,label="$T$, no feedback")
plt.plot(time/year,T_plot,'b-',markersize=1,label="T, with feedback")
plt.xlabel('years');
plt.ylabel('$T$ ($^\\circ$K)');
plt.ylim([286,300])
#plt.title('$T$');
plt.legend()
plt.grid(lw=0.25)
axes=plt.gca()


plt.subplot(2,2,4)
plt.plot(time_no_feedback/year,T_a_plot_no_feedback,'b--',markersize=1,label="$T_a$, no feedback")
plt.plot(time/year,T_a_plot,'b-',markersize=1,label="$T_a$, with feedback")
plt.xlabel('years');
plt.ylabel('$T_a$ ($^\\circ$K)');
plt.ylim([240,255])
#plt.title('$T_a$');
plt.legend()
plt.grid(lw=0.25)
axes=plt.gca()



plt.tight_layout()
plt.show()



##<font color="green"> 2) Print out the values of the model</font>
1. Print T at the surface and T in the atmosphere at year 0, year 50, year 150, year 195 with no cloud feedbacks (dashed blue line).
2.  Print T at the surface and T in the atmosphere at year 0, year 50, year 150, year 195 with cloud feedbacks (solid blue line).
3. Print the difference between the two and make a pandas dataframe of your results.


In [ ]:
T_plot_no_feedback